In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib
import matplotlib.pyplot as plt 
import matplotlib.pyplot as plt1 

import statistics
import os

###############################################
from peakutils import indexes
from peakutils import baseline
from scipy.signal import find_peaks as fp
from scipy.signal import  peak_widths

from scipy.signal import savgol_filter 

###############################################
from bokeh.plotting import figure , show
from pybaselines import whittaker as pl



from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

In [3]:
def load_data(folder_path):
    # List to store DataFrames for intensity columns
    intensity_dfs = []

    # List to store CSV file names
    csv_file_names = []

    # Loop through each file in the folder
    for file_name in os.listdir(folder_path):
        if file_name.endswith('.csv'):
            file_path = os.path.join(folder_path, file_name)
            
            # Read CSV file into a DataFrame
            df = pd.read_csv(file_path)
            
            # Extract intensity column and store it in the list
            intensity_dfs.append(df.iloc[:, 1])  # Assuming intensity is in the second column
            
            # Store CSV file name
            csv_file_names.append(os.path.splitext(file_name)[0])

    # Read the wavelength column from the first CSV file
    wavelength_df = pd.read_csv(os.path.join(folder_path, os.listdir(folder_path)[1]), usecols=[0])

    # Concatenate wavelength column with intensity columns
    result_df = pd.concat([wavelength_df] + intensity_dfs, axis=1)

    # Rename the columns with CSV file names
    column_names = ['wavelength'] + [f'{csv_file_names[i]}' for i in range(len(intensity_dfs))]

    result_df.columns = column_names
    # result_df.reset_index(drop=True, inplace=True)

    return result_df

In [4]:
SAMPLE1_Raw_df = load_data('Batch_2/sample_1')
###################################################
SAMPLE2_Raw_df = load_data('Batch_2/sample_2')
###################################################
SAMPLE3_Raw_df = load_data('Batch_2/sample_3')
###################################################
SAMPLE4_Raw_df = load_data('Batch_2/sample_4')
###################################################
SAMPLE5_Raw_df = load_data('Batch_2/sample_5')
###################################################
SAMPLE6_Raw_df = load_data('Batch_2/sample_6')
###################################################
SAMPLE7_Raw_df = load_data('Batch_2/sample_7')
####################################################
SAMPLE8_Raw_df = load_data('Batch_2/sample_8')
####################################################
SAMPLE9_Raw_df = load_data('Batch_3/sample_9')
####################################################
SAMPLE10_Raw_df = load_data('Batch_3/sample_10')
####################################################
SAMPLE11_Raw_df = load_data('Batch_3/sample_11')
####################################################
SAMPLE12_Raw_df = load_data('Batch_3/sample_12')
####################################################
SAMPLE13_Raw_df = load_data('Batch_3/sample_13')
####################################################
SAMPLE14_Raw_df = load_data('Batch_3/sample_14')
####################################################
SAMPLE15_Raw_df = load_data('Batch_3/sample_15')
####################################################
SAMPLE16_Raw_df = load_data('Batch_3/sample_16')
####################################################
SAMPLE17_Raw_df = load_data('Batch_3/sample_17')
####################################################

SAMPLE1_Raw_df


wavelength  sample1_10  sample1_11  sample1_12  sample1_9  sample1_8  \
0      180.000000         0.0         0.0         0.0        0.0        0.0   
1      180.033333         0.0         0.0         0.0        0.0        0.0   
2      180.066667         0.0         0.0         0.0        0.0        0.0   
3      180.100000         0.0         0.0         0.0        0.0        0.0   
4      180.133333         0.0         0.0         0.0        0.0        0.0   
...           ...         ...         ...         ...        ...        ...   
23426  960.866667         0.0         0.0         0.0        0.0        0.0   
23427  960.900000         0.0         0.0         0.0        0.0        0.0   
23428  960.933333         0.0         0.0         0.0        0.0        0.0   
23429  960.966667         0.0         0.0         0.0        0.0        0.0   
23430  961.000000         0.0         0.0         0.0        0.0        0.0   

       sample1_5  sample1_4  sample1_6  sample1_7  sample1_3  sample1_2  \
0            0.0        0.0        0.0        0.0        0.0        0.0   
1            0.0        0.0        0.0        0.0        0.0        0.0   
2            0.0        0.0        0.0        0.0        0.0        0.0   
3            0.0        0.0        0.0        0.0        0.0        0.0   
4            0.0        0.0        0.0        0.0        0.0        0.0   
...          ...        ...        ...        ...        ...        ...   
23426        0.0        0.0        0.0        0.0        0.0        0.0   
23427        0.0        0.0        0.0        0.0        0.0        0.0   
23428        0.0        0.0        0.0        0.0        0.0        0.0   
23429        0.0        0.0        0.0        0.0        0.0        0.0   
23430        0.0        0.0        0.0        0.0        0.0        0.0   

       sample1_1  
0            0.0  
1            0.0  
2            0.0  
3            0.0  
4            0.0  
...          ...  
23426        0.0  
23427        0.0  
23428        0.0  
23429        0.0  
23430        0.0  

[23431 rows x 13 columns]

In [5]:
import numpy as np

# Assuming you have dataframes named SAMPLE1_Raw_df, SAMPLE2_Raw_df, etc.
# Store them in a dictionary
datafram = {
    1: SAMPLE1_Raw_df,
    2: SAMPLE2_Raw_df,
    3: SAMPLE3_Raw_df,
    4: SAMPLE4_Raw_df,
    5: SAMPLE5_Raw_df,
    6: SAMPLE6_Raw_df,
    7: SAMPLE7_Raw_df,
    8: SAMPLE8_Raw_df,
    9: SAMPLE9_Raw_df,
    10: SAMPLE10_Raw_df,
    11: SAMPLE11_Raw_df,
    12: SAMPLE12_Raw_df,
    13: SAMPLE13_Raw_df,
    14: SAMPLE14_Raw_df,
    15: SAMPLE15_Raw_df,
    16: SAMPLE16_Raw_df,
    17: SAMPLE17_Raw_df,   
    # Add entries for other samples
}

# Define the sample number you want to process
sample_number = 1 # Replace with any sample number (e.g., 3, 4, ..., 17)

# Get the dataframe for the specified sample number
df_sample = datafram[sample_number]

# Construct the column name based on the sample number
column_name = f'sample{sample_number}_6'

# Filter the dataframe to get the noise list
noise_list = df_sample.loc[df_sample['wavelength'] < 195.0, column_name]

# Calculate the RMS intensity noise
RMS_intensity_noise = np.sqrt(np.mean((noise_list)**2))

# Print the RMS intensity noise
print(RMS_intensity_noise)


165.9189154198269


In [6]:

# #METHOD  - Scipy

# Threshold = 20 #(Noise Intensity * Threshold) Value for signal filtering
# height_2 = None
# Peak_Prominenace = (Threshold * RMS_intensity_noise) # #Uses S/N ratio , as comapred to other peaks
# minimum_distance_3 = None   #minimum distance between two peaks

# Sample_Peak, info = fp(SAMPLE2_Raw_df.sample2_6,height=height_2,prominence=Peak_Prominenace,distance=minimum_distance_3,width=0.1)


# Selected_Sample_Spectra = SAMPLE2_Raw_df.iloc[Sample_Peak] 

# Sample_Spectra_Peaks = figure(title = 'Peaks in hLIBS Spectra', x_axis_label = 'Wavelength' , y_axis_label = 'Intensity')
# Sample_Spectra_Peaks.line(SAMPLE2_Raw_df.wavelength,SAMPLE2_Raw_df.sample2_6 , line_width = 2, color ="green" )
# Sample_Spectra_Peaks.circle(Selected_Sample_Spectra.wavelength , Selected_Sample_Spectra.sample2_6 , color = 'red' , size = 8)

# Sample_Spectra_Peaks.width = 1200
# Sample_Spectra_Peaks.height = 600

# print(Selected_Sample_Spectra)
# show(Sample_Spectra_Peaks)


# Define the threshold and other parameters for peak finding
Threshold = 5 # (Noise Intensity * Threshold) Value for signal filtering
height_2 = None
Peak_Prominenace = (Threshold * RMS_intensity_noise)  # Uses S/N ratio, as compared to other peaks
minimum_distance_3 = None  # Minimum distance between two peaks

# Find the peaks
Sample_Peak, info = fp(df_sample[column_name], height=height_2, prominence=Peak_Prominenace, distance=minimum_distance_3, width=0.1)

# Select the sample spectra
Selected_Sample_Spectra = df_sample.iloc[Sample_Peak]

# Create the plot
Sample_Spectra_Peaks = figure(title='Peaks in hLIBS Spectra', x_axis_label='Wavelength', y_axis_label='Intensity')
Sample_Spectra_Peaks.line(df_sample['wavelength'], df_sample[column_name], line_width=2, color="green")
Sample_Spectra_Peaks.circle(Selected_Sample_Spectra['wavelength'], Selected_Sample_Spectra[column_name], color='red', size=5)

Sample_Spectra_Peaks.width = 1200
Sample_Spectra_Peaks.height = 600

# Print the selected sample spectra
print(Selected_Sample_Spectra)

# Show the plot
show(Sample_Spectra_Peaks)



       wavelength   sample1_10   sample1_11   sample1_12    sample1_9  \
601    200.033333  1660.683423  1780.601469  1735.864034  1314.921826   
633    201.100000  1516.023496  1627.676407  1580.858202  1196.785549   
656    201.866667  1060.269791  1133.634151  1109.780831   825.198867   
677    202.566667   988.841960  1273.840742  1686.555398   846.963669   
698    203.266667  1030.711024  1105.961738  1073.940502   820.425824   
...           ...          ...          ...          ...          ...   
19825  840.833333  6300.253993  6603.109995  6403.913647  3881.102347   
19874  842.466667  8139.510676  8523.698423  8333.055464  4968.278687   
20164  852.133333  3055.117104  3212.564788  3139.999637  1704.064299   
21968  912.266667  4634.087703  4853.637009  4716.691655  2507.105566   
22274  922.466667  1623.706138  1718.047212  1653.142998   912.609292   

         sample1_8    sample1_5    sample1_4    sample1_6    sample1_7  \
601    1735.735553  1714.475074  1753.877787  182

In [7]:
# Peak Selection and Data Trimming

In [8]:
# peak = 500.606
# peak_min = (peak - 5) 
# peak_max = (peak + 5) 

#Getting the full wavelength
Wavelength_Min = 180.000000
Wavelength_Max = 961.000000


SAMPLE1_Select_df = SAMPLE1_Raw_df[(SAMPLE1_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE1_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE2_Select_df = SAMPLE2_Raw_df[(SAMPLE2_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE2_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE3_Select_df = SAMPLE3_Raw_df[(SAMPLE3_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE3_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE4_Select_df = SAMPLE4_Raw_df[(SAMPLE4_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE4_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE5_Select_df = SAMPLE5_Raw_df[(SAMPLE5_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE5_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE6_Select_df = SAMPLE6_Raw_df[(SAMPLE6_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE6_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE7_Select_df = SAMPLE7_Raw_df[(SAMPLE7_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE7_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE8_Select_df = SAMPLE8_Raw_df[(SAMPLE8_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE8_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE9_Select_df = SAMPLE9_Raw_df[(SAMPLE9_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE9_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE10_Select_df = SAMPLE10_Raw_df[(SAMPLE10_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE10_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE11_Select_df = SAMPLE11_Raw_df[(SAMPLE11_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE11_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE12_Select_df = SAMPLE12_Raw_df[(SAMPLE12_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE12_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE13_Select_df = SAMPLE13_Raw_df[(SAMPLE13_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE13_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE14_Select_df = SAMPLE14_Raw_df[(SAMPLE14_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE14_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE15_Select_df = SAMPLE15_Raw_df[(SAMPLE15_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE15_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE16_Select_df = SAMPLE16_Raw_df[(SAMPLE16_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE16_Raw_df['wavelength'] <= Wavelength_Max)]
SAMPLE17_Select_df = SAMPLE17_Raw_df[(SAMPLE17_Raw_df['wavelength'] >= Wavelength_Min) & (SAMPLE17_Raw_df['wavelength'] <= Wavelength_Max)]




SAMPLE1_Select_df

wavelength  sample1_10  sample1_11  sample1_12  sample1_9  sample1_8  \
0      180.000000         0.0         0.0         0.0        0.0        0.0   
1      180.033333         0.0         0.0         0.0        0.0        0.0   
2      180.066667         0.0         0.0         0.0        0.0        0.0   
3      180.100000         0.0         0.0         0.0        0.0        0.0   
4      180.133333         0.0         0.0         0.0        0.0        0.0   
...           ...         ...         ...         ...        ...        ...   
23426  960.866667         0.0         0.0         0.0        0.0        0.0   
23427  960.900000         0.0         0.0         0.0        0.0        0.0   
23428  960.933333         0.0         0.0         0.0        0.0        0.0   
23429  960.966667         0.0         0.0         0.0        0.0        0.0   
23430  961.000000         0.0         0.0         0.0        0.0        0.0   

       sample1_5  sample1_4  sample1_6  sample1_7  sample1_3  sample1_2  \
0            0.0        0.0        0.0        0.0        0.0        0.0   
1            0.0        0.0        0.0        0.0        0.0        0.0   
2            0.0        0.0        0.0        0.0        0.0        0.0   
3            0.0        0.0        0.0        0.0        0.0        0.0   
4            0.0        0.0        0.0        0.0        0.0        0.0   
...          ...        ...        ...        ...        ...        ...   
23426        0.0        0.0        0.0        0.0        0.0        0.0   
23427        0.0        0.0        0.0        0.0        0.0        0.0   
23428        0.0        0.0        0.0        0.0        0.0        0.0   
23429        0.0        0.0        0.0        0.0        0.0        0.0   
23430        0.0        0.0        0.0        0.0        0.0        0.0   

       sample1_1  
0            0.0  
1            0.0  
2            0.0  
3            0.0  
4            0.0  
...          ...  
23426        0.0  
23427        0.0  
23428        0.0  
23429        0.0  
23430        0.0  

[23431 rows x 13 columns]

In [9]:
Selected_df_Plot = figure(title = 'Selected Data Plot' , x_axis_label = 'Wavelength' , y_axis_label = 'Intensity')

Selected_df_Plot.line(SAMPLE1_Select_df.wavelength,SAMPLE1_Select_df.sample1_6 , line_width = 2, color ="blue" )
#####################################################################################################################
Selected_df_Plot.line(SAMPLE2_Select_df.wavelength,SAMPLE2_Select_df.sample2_6 , line_width = 2, color ="orange" )
###############################################################################################################
Selected_df_Plot.line(SAMPLE3_Select_df.wavelength,SAMPLE3_Select_df.sample3_6 , line_width = 2, color ="green")
######################################################################################################################
Selected_df_Plot.line(SAMPLE4_Select_df.wavelength,SAMPLE4_Select_df.sample4_6 , line_width = 2, color ="red")
##############################################################################################################
Selected_df_Plot.line(SAMPLE5_Select_df.wavelength,SAMPLE5_Select_df.sample5_6 , line_width = 2, color ="purple")
###############################################################################################################
Selected_df_Plot.line(SAMPLE6_Select_df.wavelength,SAMPLE6_Select_df.sample6_6 , line_width = 2, color ="brown")
####################################################################################################################
Selected_df_Plot.line(SAMPLE7_Select_df.wavelength,SAMPLE7_Select_df.sample7_6 , line_width = 2, color ="pink")
##################################################################################################################
Selected_df_Plot.line(SAMPLE8_Select_df.wavelength,SAMPLE8_Select_df.sample8_6 , line_width = 2, color ="gray")
###################################################################################################################
Selected_df_Plot.line(SAMPLE9_Select_df.wavelength,SAMPLE9_Select_df.sample9_6 , line_width = 2, color ="olive")
###################################################################################################################
Selected_df_Plot.line(SAMPLE10_Select_df.wavelength,SAMPLE10_Select_df.sample10_6 , line_width = 2, color ="Cyan")
###################################################################################################################
Selected_df_Plot.line(SAMPLE11_Select_df.wavelength,SAMPLE11_Select_df.sample11_6 , line_width = 2, color ="black")
###################################################################################################################
Selected_df_Plot.line(SAMPLE12_Select_df.wavelength,SAMPLE12_Select_df.sample12_6 , line_width = 2, color ="tomato")
###################################################################################################################
Selected_df_Plot.line(SAMPLE13_Select_df.wavelength,SAMPLE13_Select_df.sample13_6 , line_width = 2, color ="steelblue")
###################################################################################################################
Selected_df_Plot.line(SAMPLE14_Select_df.wavelength,SAMPLE14_Select_df.sample14_6 , line_width = 2, color ="limegreen")
###################################################################################################################
Selected_df_Plot.line(SAMPLE15_Select_df.wavelength,SAMPLE15_Select_df.sample15_6 , line_width = 2, color ="deeppink")
###################################################################################################################
Selected_df_Plot.line(SAMPLE16_Select_df.wavelength,SAMPLE16_Select_df.sample16_6 , line_width = 2, color ="gold")
###################################################################################################################
Selected_df_Plot.line(SAMPLE17_Select_df.wavelength,SAMPLE17_Select_df.sample17_6 , line_width = 2, color ="indigo")
###################################################################################################################

Selected_df_Plot.width = 1200
Selected_df_Plot.height = 500
show(Selected_df_Plot)

# Data Preprocessing of the Spectra

In [10]:
def baseline_correction(df):
    """
    Perform baseline correction on the intensity columns of the input DataFrame and create a new DataFrame with corrected values.
    
    Parameters:
        df (DataFrame): Input DataFrame containing the wavelength and intensity columns.
        
    Returns:
        DataFrame: New DataFrame with baseline-corrected intensity columns and the same wavelength column as the input DataFrame.
    """
    # Copy the 'wavelength' column from the input DataFrame
    new_df = pd.DataFrame({'wavelength': df['wavelength']})
    
    # Perform baseline correction for each intensity column and add them to the new DataFrame
    for col in df.columns[1:]:  # Exclude the 'wavelength' column
        baseline, _ = pl.airpls(df[col])
        corrected_values = df[col] - baseline
        new_df[col] = corrected_values
    
    return new_df

In [11]:
SAMPLE1_BaselineCorrected_df = baseline_correction(SAMPLE1_Raw_df)
SAMPLE2_BaselineCorrected_df = baseline_correction(SAMPLE2_Raw_df)
SAMPLE3_BaselineCorrected_df = baseline_correction(SAMPLE3_Raw_df)
SAMPLE4_BaselineCorrected_df = baseline_correction(SAMPLE4_Raw_df)
SAMPLE5_BaselineCorrected_df = baseline_correction(SAMPLE5_Raw_df)
SAMPLE6_BaselineCorrected_df = baseline_correction(SAMPLE6_Raw_df)
SAMPLE7_BaselineCorrected_df = baseline_correction(SAMPLE7_Raw_df)
SAMPLE8_BaselineCorrected_df = baseline_correction(SAMPLE8_Raw_df)
SAMPLE9_BaselineCorrected_df = baseline_correction(SAMPLE9_Raw_df)
SAMPLE10_BaselineCorrected_df = baseline_correction(SAMPLE10_Raw_df)
SAMPLE11_BaselineCorrected_df = baseline_correction(SAMPLE11_Raw_df)
SAMPLE12_BaselineCorrected_df = baseline_correction(SAMPLE12_Raw_df)
SAMPLE13_BaselineCorrected_df = baseline_correction(SAMPLE13_Raw_df)
SAMPLE14_BaselineCorrected_df = baseline_correction(SAMPLE14_Raw_df)
SAMPLE15_BaselineCorrected_df = baseline_correction(SAMPLE15_Raw_df)
SAMPLE16_BaselineCorrected_df = baseline_correction(SAMPLE16_Raw_df)
SAMPLE17_BaselineCorrected_df = baseline_correction(SAMPLE17_Raw_df)

SAMPLE1_BaselineCorrected_df

wavelength  sample1_10  sample1_11  sample1_12  sample1_9   sample1_8  \
0      180.000000  120.605185  125.345354  123.832448  90.970942  123.312688   
1      180.033333  120.070018  124.790085  123.283574  90.567980  122.766679   
2      180.066667  119.534852  124.234815  122.734699  90.165018  122.220670   
3      180.100000  118.999685  123.679546  122.185825  89.762055  121.674661   
4      180.133333  118.464519  123.124276  121.636950  89.359093  121.128652   
...           ...         ...         ...         ...        ...         ...   
23426  960.866667    0.535364    0.565683    0.561261   0.372895    0.535766   
23427  960.900000    0.477813    0.504832    0.500964   0.333312    0.478816   
23428  960.933333    0.420260    0.443979    0.440664   0.293728    0.421865   
23429  960.966667    0.362706    0.383125    0.380364   0.254142    0.364912   
23430  961.000000    0.305152    0.322271    0.320063   0.214557    0.307960   

        sample1_5   sample1_4   sample1_6   sample1_7   sample1_3   sample1_2  \
0      118.537351  116.953769  125.094039  131.509287  119.649332  105.932936   
1      118.012267  116.436331  124.540092  130.926558  119.120030  105.460701   
2      117.487182  115.918893  123.986144  130.343829  118.590727  104.988466   
3      116.962098  115.401455  123.432197  129.761100  118.061425  104.516231   
4      116.437014  114.884016  122.878249  129.178371  117.532122  104.043996   
...           ...         ...         ...         ...         ...         ...   
23426    0.606444    0.505279    0.648909    0.632793    0.542795    0.614836   
23427    0.553328    0.452122    0.592125    0.577387    0.485716    0.560981   
23428    0.500209    0.398963    0.535338    0.521978    0.428635    0.507123   
23429    0.447088    0.345803    0.478550    0.466567    0.371554    0.453265   
23430    0.393968    0.292643    0.421761    0.411157    0.314471    0.399405   

       sample1_1  
0      97.980548  
1      97.542889  
2      97.105230  
3      96.667571  
4      96.229911  
...          ...  
23426   0.561074  
23427   0.511927  
23428   0.462778  
23429   0.413628  
23430   0.364477  

[23431 rows x 13 columns]

In [12]:
def standard_normal_variate_normalization(df):
    # Select columns containing intensities
    intensity_cols = df.columns[1:]  #  columns 2 to 13 are intensities and are stored in intensity_cols

    # SVN normalization
    for col in intensity_cols:
        mean_intensity = df[col].mean()
        std_intensity = df[col].std()
        df[col] = (df[col] - mean_intensity) / std_intensity

    return df

In [13]:
def total_intensity_normalization(df):
    # Selecting only the intensity columns (assuming the first column is wavelength)
    intensities = df.iloc[:, 1:]  

    # Initialize an empty DataFrame to store normalized intensities
    normalized_intensities = pd.DataFrame()

    # Iterate over each column (each spectrum)
    for column in intensities.columns:
        spectrum = intensities[column]
        total_intensity = spectrum.sum()
        
        # Normalize the spectrum by dividing each intensity value by the total intensity
        normalized_spectrum = spectrum / total_intensity
        
        # Append the normalized spectrum to the DataFrame of normalized intensities
        normalized_intensities[column] = normalized_spectrum

    # Combine the wavelength column with normalized intensities
    normalized_df = pd.concat([df.iloc[:, 0], normalized_intensities], axis=1)

    return normalized_df

In [14]:
def unit_norm_normalization(df):
    # Selecting only the intensity columns (assuming the first column is wavelength)
    intensities_1 = df.iloc[:, 1:]  
    
    # Initialize an empty DataFrame to store normalized intensities
    normalized_intensities_1 = pd.DataFrame()

    # Iterate over each column (each spectrum)
    for column_1 in intensities_1.columns:
        spectrum_1 = intensities_1[column_1]
        
        # Calculate the norm of the spectrum using a simple equation
        spectrum_norm = np.sqrt(np.sum(spectrum_1 ** 2))
        
        # Normalize the spectrum by dividing each intensity value by its norm
        normalized_spectrum_1 = spectrum_1 / spectrum_norm
        
        # Assign the normalized spectrum to the DataFrame of normalized intensities
        normalized_intensities_1[column_1] = normalized_spectrum_1

    # Combine the wavelength column with normalized intensities
    normalized_df_1 = pd.concat([df.iloc[:, 0], normalized_intensities_1], axis=1)
    
    return normalized_df_1

In [15]:
def max_intensity_normalization(df):
    # Selecting only the intensity columns (assuming the first column is wavelength)
    intensities_2 = df.iloc[:, 1:]  

    # Initialize an empty DataFrame to store normalized intensities
    normalized_intensities_2 = pd.DataFrame()

    # Iterate over each column (each spectrum)
    for column_2 in intensities_2.columns:
        spectrum_2 = intensities_2[column_2]
        
        # Find the maximum intensity value in the spectrum
        max_intensity = spectrum_2.max()
        
        # Normalize the spectrum by dividing each intensity value by the maximum intensity
        normalized_spectrum_2 = spectrum_2 / max_intensity
        
        # Assign the normalized spectrum to the DataFrame of normalized intensities
        normalized_intensities_2[column_2] = normalized_spectrum_2

    # Combine the wavelength column with normalized intensities
    normalized_df_2 = pd.concat([df.iloc[:, 0], normalized_intensities_2], axis=1)

    return normalized_df_2

In [16]:
SAMPLE1_Normalized_df = unit_norm_normalization(SAMPLE1_BaselineCorrected_df)
SAMPLE2_Normalized_df = unit_norm_normalization(SAMPLE2_BaselineCorrected_df)
SAMPLE3_Normalized_df = unit_norm_normalization(SAMPLE3_BaselineCorrected_df)
SAMPLE4_Normalized_df = unit_norm_normalization(SAMPLE4_BaselineCorrected_df)
SAMPLE5_Normalized_df = unit_norm_normalization(SAMPLE5_BaselineCorrected_df)
SAMPLE6_Normalized_df = unit_norm_normalization(SAMPLE6_BaselineCorrected_df)
SAMPLE7_Normalized_df = unit_norm_normalization(SAMPLE7_BaselineCorrected_df)
SAMPLE8_Normalized_df = unit_norm_normalization(SAMPLE8_BaselineCorrected_df)
SAMPLE9_Normalized_df = unit_norm_normalization(SAMPLE9_BaselineCorrected_df)
SAMPLE10_Normalized_df = unit_norm_normalization(SAMPLE10_BaselineCorrected_df)
SAMPLE11_Normalized_df = unit_norm_normalization(SAMPLE11_BaselineCorrected_df)
SAMPLE12_Normalized_df = unit_norm_normalization(SAMPLE12_BaselineCorrected_df)
SAMPLE13_Normalized_df = unit_norm_normalization(SAMPLE13_BaselineCorrected_df)
SAMPLE14_Normalized_df = unit_norm_normalization(SAMPLE14_BaselineCorrected_df)
SAMPLE15_Normalized_df = unit_norm_normalization(SAMPLE15_BaselineCorrected_df)
SAMPLE16_Normalized_df = unit_norm_normalization(SAMPLE16_BaselineCorrected_df)
SAMPLE17_Normalized_df = unit_norm_normalization(SAMPLE17_BaselineCorrected_df)

SAMPLE1_Normalized_df

wavelength    sample1_10    sample1_11    sample1_12     sample1_9  \
0      180.000000  3.089015e-04  3.151475e-04  3.154714e-04  2.928374e-04   
1      180.033333  3.075308e-04  3.137514e-04  3.140731e-04  2.915402e-04   
2      180.066667  3.061601e-04  3.123553e-04  3.126749e-04  2.902431e-04   
3      180.100000  3.047894e-04  3.109592e-04  3.112766e-04  2.889459e-04   
4      180.133333  3.034187e-04  3.095632e-04  3.098783e-04  2.876488e-04   
...           ...           ...           ...           ...           ...   
23426  960.866667  1.371207e-06  1.422260e-06  1.429850e-06  1.200357e-06   
23427  960.900000  1.223804e-06  1.269267e-06  1.276239e-06  1.072938e-06   
23428  960.933333  1.076396e-06  1.116268e-06  1.122622e-06  9.455152e-07   
23429  960.966667  9.289855e-07  9.632669e-07  9.690020e-07  8.180899e-07   
23430  961.000000  7.815741e-07  8.102649e-07  8.153815e-07  6.906640e-07   

          sample1_8     sample1_5     sample1_4  sample1_6  sample1_7  \
0      3.099002e-04  2.975043e-04  2.918906e-04   0.000313   0.000326   
1      3.085280e-04  2.961864e-04  2.905992e-04   0.000312   0.000324   
2      3.071558e-04  2.948686e-04  2.893078e-04   0.000310   0.000323   
3      3.057836e-04  2.935507e-04  2.880164e-04   0.000309   0.000322   
4      3.044114e-04  2.922329e-04  2.867250e-04   0.000308   0.000320   
...             ...           ...           ...        ...        ...   
23426  1.346447e-06  1.522049e-06  1.261063e-06   0.000002   0.000002   
23427  1.203326e-06  1.388738e-06  1.128395e-06   0.000001   0.000001   
23428  1.060199e-06  1.255421e-06  9.957227e-07   0.000001   0.000001   
23429  9.170706e-07  1.122100e-06  8.630476e-07   0.000001   0.000001   
23430  7.739410e-07  9.887780e-07  7.303718e-07   0.000001   0.000001   

          sample1_3     sample1_2     sample1_1  
0      2.953234e-04  2.622029e-04  2.508832e-04  
1      2.940169e-04  2.610341e-04  2.497625e-04  
2      2.927105e-04  2.598652e-04  2.486419e-04  
3      2.914040e-04  2.586963e-04  2.475212e-04  
4      2.900976e-04  2.575275e-04  2.464006e-04  
...             ...           ...           ...  
23426  1.339749e-06  1.521829e-06  1.436653e-06  
23427  1.198865e-06  1.388528e-06  1.310810e-06  
23428  1.057976e-06  1.255221e-06  1.184962e-06  
23429  9.170838e-07  1.121911e-06  1.059111e-06  
23430  7.761912e-07  9.885997e-07  9.332587e-07  

[23431 rows x 13 columns]

In [17]:
def average_intensity(df, intensity_name):
    # Select intensity columns (from column 2 to column 13)
    intensity_columns = df.columns[1:]

    # Calculate the mean of intensity columns
    averaged_intensity = df[intensity_columns].mean(axis=1)

    # Create a new DataFrame with wavelength and averaged intensity
    averaged_df = pd.DataFrame({'wavelength': df['wavelength'], intensity_name: averaged_intensity})

    return averaged_df

In [18]:
SAMPLE1_Averaged_df = average_intensity(df = SAMPLE1_Normalized_df , intensity_name= 'sample1')
SAMPLE2_Averaged_df = average_intensity(df = SAMPLE2_Normalized_df , intensity_name= 'sample2')
SAMPLE3_Averaged_df = average_intensity(df = SAMPLE3_Normalized_df , intensity_name= 'sample3')
SAMPLE4_Averaged_df = average_intensity(df = SAMPLE4_Normalized_df , intensity_name= 'sample4')
SAMPLE5_Averaged_df = average_intensity(df = SAMPLE5_Normalized_df , intensity_name= 'sample5')
SAMPLE6_Averaged_df = average_intensity(df = SAMPLE6_Normalized_df , intensity_name= 'sample6')
SAMPLE7_Averaged_df = average_intensity(df = SAMPLE7_Normalized_df , intensity_name= 'sample7')
SAMPLE8_Averaged_df = average_intensity(df = SAMPLE8_Normalized_df , intensity_name= 'sample8')
SAMPLE9_Averaged_df = average_intensity(df = SAMPLE9_Normalized_df , intensity_name= 'sample9')
SAMPLE10_Averaged_df = average_intensity(df = SAMPLE10_Normalized_df , intensity_name= 'sample10')
SAMPLE11_Averaged_df = average_intensity(df = SAMPLE11_Normalized_df , intensity_name= 'sample11')
SAMPLE12_Averaged_df = average_intensity(df = SAMPLE12_Normalized_df , intensity_name= 'sample12')
SAMPLE13_Averaged_df = average_intensity(df = SAMPLE13_Normalized_df , intensity_name= 'sample13')
SAMPLE14_Averaged_df = average_intensity(df = SAMPLE14_Normalized_df , intensity_name= 'sample14')
SAMPLE15_Averaged_df = average_intensity(df = SAMPLE15_Normalized_df , intensity_name= 'sample15')
SAMPLE16_Averaged_df = average_intensity(df = SAMPLE16_Normalized_df , intensity_name= 'sample16')
SAMPLE17_Averaged_df = average_intensity(df = SAMPLE17_Normalized_df , intensity_name= 'sample17')

print(SAMPLE1_Averaged_df)

       wavelength       sample1
0      180.000000  2.982602e-04
1      180.033333  2.969376e-04
2      180.066667  2.956151e-04
3      180.100000  2.942926e-04
4      180.133333  2.929700e-04
...           ...           ...
23426  960.866667  1.420343e-06
23427  960.900000  1.281175e-06
23428  960.933333  1.142001e-06
23429  960.966667  1.002825e-06
23430  961.000000  8.636482e-07

[23431 rows x 2 columns]


In [19]:

# List of DataFrame names
data_frames = [SAMPLE1_Averaged_df, SAMPLE2_Averaged_df, SAMPLE3_Averaged_df, 
               SAMPLE4_Averaged_df, SAMPLE5_Averaged_df, SAMPLE6_Averaged_df, 
               SAMPLE7_Averaged_df, SAMPLE8_Averaged_df ,SAMPLE9_Averaged_df,
               SAMPLE10_Averaged_df,SAMPLE11_Averaged_df,SAMPLE12_Averaged_df,
               SAMPLE13_Averaged_df,SAMPLE14_Averaged_df,SAMPLE15_Averaged_df,
               SAMPLE16_Averaged_df,SAMPLE17_Averaged_df]

# Initialize the new DataFrame with the 'wavelength' column from the first DataFrame
new_df = data_frames[0][['wavelength']].copy()

# Add 'sample' columns from each DataFrame
for i, df in enumerate(data_frames):
    sample_column = f'sample{i+1}'
    new_df[sample_column] = df[sample_column]

# Display the new DataFrame
print(new_df)

       wavelength       sample1       sample2       sample3   sample4  \
0      180.000000  2.982602e-04  3.173441e-04  3.296180e-04  0.000406   
1      180.033333  2.969376e-04  3.159363e-04  3.281510e-04  0.000404   
2      180.066667  2.956151e-04  3.145284e-04  3.266841e-04  0.000402   
3      180.100000  2.942926e-04  3.131205e-04  3.252171e-04  0.000400   
4      180.133333  2.929700e-04  3.117126e-04  3.237502e-04  0.000399   
...           ...           ...           ...           ...       ...   
23426  960.866667  1.420343e-06  1.277433e-06  1.497406e-06  0.000002   
23427  960.900000  1.281175e-06  1.140021e-06  1.355714e-06  0.000001   
23428  960.933333  1.142001e-06  1.002604e-06  1.214016e-06  0.000001   
23429  960.966667  1.002825e-06  8.651848e-07  1.072315e-06  0.000001   
23430  961.000000  8.636482e-07  7.277650e-07  9.306132e-07  0.000001   

            sample5       sample6   sample7   sample8   sample9  sample10  \
0      2.642275e-04  3.323073e-04  0.000291  0

# SELECTION OF PEAKS , TO DETERMINE THE PEAK START AND STOP 

# Wavelengths for Detected Peak(red circles above)

In [20]:
Sample_Spectra_List = []

for iteam in Selected_Sample_Spectra.wavelength:
    iteam = float(iteam)
    Sample_Spectra_List.append(iteam)
    
print(Sample_Spectra_List)


[200.0333333333322, 201.0999999999988, 201.86666666666545, 202.56666666666536, 203.26666666666532, 204.0666666666653, 205.09999999999857, 205.5666666666652, 206.23333333333184, 208.76666666666503, 211.0666666666649, 213.8333333333314, 215.06666666666467, 216.1666666666646, 216.66666666666455, 217.5333333333312, 217.79999999999785, 218.66666666666447, 219.19999999999777, 219.5666666666644, 220.0666666666644, 220.86666666666437, 221.36666666666432, 222.03333333333092, 222.86666666666423, 223.3666666666642, 224.9333333333308, 225.1666666666641, 225.56666666666408, 225.99999999999736, 226.4333333333307, 226.73333333333068, 227.96666666666397, 228.39999999999725, 229.3999999999972, 229.7999999999972, 231.13333333333043, 232.699999999997, 233.2333333333303, 233.7999999999969, 234.03333333333023, 234.3666666666636, 234.79999999999688, 235.09999999999687, 235.4666666666635, 235.96666666666349, 236.43333333333013, 236.86666666666343, 237.33333333333007, 237.5333333333301, 237.8999999999967, 238

In [21]:
Selected_Sample_Spectra_min_list = []

Selected_Sample_Spectra_left = SAMPLE1_Averaged_df.iloc[info['left_ips']] 
Selected_Sample_Spectra_min_list = (Selected_Sample_Spectra_left['wavelength']).tolist()

print (Selected_Sample_Spectra_min_list)



[199.96666666666556, 200.9999999999988, 201.76666666666543, 202.4666666666654, 203.16666666666532, 203.9666666666653, 205.0333333333319, 205.4666666666652, 206.0999999999985, 208.66666666666504, 210.9666666666649, 213.76666666666475, 214.96666666666468, 216.09999999999795, 216.5666666666646, 217.4333333333312, 217.69999999999783, 218.56666666666447, 219.09999999999775, 219.49999999999773, 219.9666666666644, 220.76666666666435, 221.29999999999765, 221.93333333333092, 222.7333333333309, 223.2666666666642, 224.8333333333308, 225.0333333333308, 225.46666666666408, 225.8999999999974, 226.2333333333307, 226.63333333333068, 227.86666666666397, 228.29999999999723, 229.33333333333053, 229.6999999999972, 231.03333333333043, 232.599999999997, 233.09999999999695, 233.69999999999692, 233.9666666666636, 234.23333333333025, 234.6999999999969, 234.99999999999687, 235.36666666666352, 235.83333333333016, 236.33333333333013, 236.76666666666344, 237.2666666666634, 237.4666666666634, 237.83333333333005, 23

In [22]:
Selected_Sample_Spectra_max_list = []


Selected_Sample_Spectra_right = SAMPLE1_Averaged_df.iloc[info['right_ips']] 
Selected_Sample_Spectra_max_list = (Selected_Sample_Spectra_right['wavelength']).tolist()

print (Selected_Sample_Spectra_max_list)

[200.0999999999989, 201.13333333333213, 202.13333333333208, 202.63333333333205, 203.333333333332, 204.133333333332, 205.16666666666524, 205.59999999999852, 206.2999999999985, 208.8333333333317, 211.1333333333316, 213.9333333333314, 215.1333333333313, 216.23333333333127, 216.73333333333125, 217.56666666666453, 217.8333333333312, 218.7666666666645, 219.2333333333311, 219.63333333333108, 220.13333333333105, 220.933333333331, 221.43333333333095, 222.0999999999976, 222.8999999999976, 223.4333333333309, 224.9666666666641, 225.29999999999745, 225.63333333333077, 226.06666666666405, 226.46666666666405, 226.7999999999973, 228.0333333333306, 228.43333333333055, 229.46666666666383, 229.8333333333305, 231.36666666666372, 232.76666666666367, 233.29999999999697, 233.83333333333027, 234.0666666666636, 234.4666666666636, 234.86666666666355, 235.1333333333302, 235.49999999999685, 236.06666666666348, 236.5333333333301, 237.0333333333301, 237.39999999999677, 237.5333333333301, 237.93333333333004, 238.333

# COMBINED LIST

In [23]:
wavelength_min_max_list = [[a, b] for a, b in zip(Selected_Sample_Spectra_min_list, Selected_Sample_Spectra_max_list)]

print(wavelength_min_max_list)



[[199.96666666666556, 200.0999999999989], [200.9999999999988, 201.13333333333213], [201.76666666666543, 202.13333333333208], [202.4666666666654, 202.63333333333205], [203.16666666666532, 203.333333333332], [203.9666666666653, 204.133333333332], [205.0333333333319, 205.16666666666524], [205.4666666666652, 205.59999999999852], [206.0999999999985, 206.2999999999985], [208.66666666666504, 208.8333333333317], [210.9666666666649, 211.1333333333316], [213.76666666666475, 213.9333333333314], [214.96666666666468, 215.1333333333313], [216.09999999999795, 216.23333333333127], [216.5666666666646, 216.73333333333125], [217.4333333333312, 217.56666666666453], [217.69999999999783, 217.8333333333312], [218.56666666666447, 218.7666666666645], [219.09999999999775, 219.2333333333311], [219.49999999999773, 219.63333333333108], [219.9666666666644, 220.13333333333105], [220.76666666666435, 220.933333333331], [221.29999999999765, 221.43333333333095], [221.93333333333092, 222.0999999999976], [222.733333333330

In [24]:

# Create a list to store the maximum peaks for each wavelength range
max_peaks_all_ranges = []

# Loop through each wavelength range
for wavelength_min, wavelength_max in wavelength_min_max_list:
    # Filter the DataFrame for the current wavelength range
    filtered_df = new_df[(new_df["wavelength"] >= wavelength_min) & (new_df["wavelength"] <= wavelength_max)]
    #print(filtered_df)
    
    
    # Find the maximum value for each sample column within the filtered DataFrame
    max_peaks = []
    for sample in filtered_df.columns[1:]:  # Skip the 'wavelength' column
        max_value = filtered_df[sample].max()
        min_value = filtered_df[sample].min()
        max_peaks.append(max_value)
    
    # Append the list of maximum peaks for this range to the main list
    max_peaks_all_ranges.append(max_peaks)

# print(max_peaks_all_ranges)
    
#Print the results
# for i, max_peaks in enumerate(max_peaks_all_ranges, start=1):
#     print(f"Range {i} max peaks: {max_peaks}")

# LIST FOR NIST ELEMENT PEAKS

In [25]:
ele = 'Si'

# NISTDB_Reference_Spectra = pd.read_csv(r"NIST_3/" + ele +".csv" , encoding = 'windows - 1252' , usecols=(3,4,5,6,7,8))
# Reference_Spectra_List = (NISTDB_Reference_Spectra['obs_wl_air(nm)']).tolist()

################################################################################################

New_Reference_Spectra = pd.read_csv(r"NIST_2/" + ele +".csv" , encoding = 'windows - 1252' , usecols=(0,1))
Reference_Spectra_List = (New_Reference_Spectra['Wavelength'] / 10).tolist()

print(Reference_Spectra_List)


[89.20009999999999, 99.2684, 119.04159999999999, 119.32898, 119.45003999999999, 122.87460000000002, 122.93879999999999, 124.84259999999999, 125.0433, 125.1164, 126.04222999999999, 126.47379000000001, 130.92766, 135.0057, 152.670698, 153.34318000000002, 159.45655, 159.49493, 162.28806, 162.9441, 162.99477, 167.52052, 169.62065, 169.79409, 177.09223, 180.801288, 181.40794, 181.6929, 183.65102, 184.1449, 184.377, 184.55203, 184.61118, 184.74737, 184.81504, 184.8748, 185.06719, 185.24717, 187.48423, 190.13377, 197.75978, 197.92056, 198.06185, 198.3233, 198.6364, 198.89937, 205.81323000000003, 207.2016, 207.2701, 220.7978, 221.08939999999998, 221.17440000000002, 221.6669, 221.80569999999997, 243.5154, 250.6897, 251.43159999999997, 251.6112, 251.92020000000002, 252.41080000000002, 252.8509, 263.1282, 288.15771, 290.4283, 290.5692, 298.7645, 305.3184, 318.897, 319.309, 319.95140000000004, 320.3872, 321.002, 333.3139, 333.9819, 385.6017, 386.2595, 390.5523, 412.8067, 413.0893, 462.172099999999

In [26]:
Reference_Spectra_Min_Max = []
Reference_Spectra_Min_Max = [[num - 0.15, num + 0.15] for num in Reference_Spectra_List]     
    
print(Reference_Spectra_Min_Max)

[[89.05009999999999, 89.3501], [99.1184, 99.4184], [118.89159999999998, 119.1916], [119.17898, 119.47898], [119.30003999999998, 119.60003999999999], [122.72460000000001, 123.02460000000002], [122.78879999999998, 123.08879999999999], [124.69259999999998, 124.9926], [124.8933, 125.19330000000001], [124.9664, 125.2664], [125.89222999999998, 126.19223], [126.32379, 126.62379000000001], [130.77766, 131.07766], [134.85569999999998, 135.1557], [152.52069799999998, 152.820698], [153.19318, 153.49318000000002], [159.30655, 159.60655], [159.34493, 159.64493000000002], [162.13806, 162.43806], [162.7941, 163.0941], [162.84476999999998, 163.14477], [167.37052, 167.67052], [169.47065, 169.77065000000002], [169.64409, 169.94409000000002], [176.94223, 177.24223], [180.651288, 180.951288], [181.25794, 181.55794], [181.5429, 181.84290000000001], [183.50101999999998, 183.80102], [183.9949, 184.2949], [184.227, 184.52700000000002], [184.40203, 184.70203], [184.46117999999998, 184.76118], [184.597369999999

In [27]:
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score, mean_squared_error
import pandas as pd

# Provided data (as an example, add more sublists as needed)
data = max_peaks_all_ranges

elements = {
    'Element': ['C'  , 'Mn', 'Si', 'Al', 'Cr', 'Cu', 'N', 'Ni' , 'Nb' ,'Mo', 'Ti'],
    'SAMPLE1': [0.15 , 1.9, 0.3, 0.04, 0.41, 0.02, 0.004, 0.030, 0.006, 0.101, 0.044],
    'SAMPLE2': [0.15 , 1.8, 0.3, 0.04, 0.42, 0.02, 0.004, 0.037, 0.006, 0.105, 0.037],
    'SAMPLE3': [0.16 , 2.3, 0.5, 0.69, 0.70, 0.03, 0.003, 0.048, 0.032, 0.023, 0.025],
    'SAMPLE4': [0.23 , 1.2, 0.2, 0.03, 0.14, 0.02, 0.004, 0.020, 0.001, 0.000, 0.034],
    'SAMPLE5': [0.21 , 1.9, 1.8, 0.04, 0.05, 0.03, 0.003, 0.037, 0.056, 0.006, 0.014],
    'SAMPLE6': [0.07 , 2.3, 0.2, 0.04, 0.60, 0.02, 0.005, 0.040, 0.001, 0.020, 0.051],
    'SAMPLE7': [0.003, 0.1, 0.0, 0.02, 0.03, 0.01, 0.002, 0.020, 0.001, 0.005, 0.068],
    'SAMPLE8': [0.06 , 1.1, 0.4, 0.04, 0.03, 0.01, 0.004, 0.010, 0.046, 0.002, 0.028],
}

# Extract 'Mn' values for samples 1 to 8
mn_values = [elements[f'SAMPLE{i}'][2] for i in range(1, 9)]
# print(mn_values)
results = []

# Loop through each sublist in data and perform linear regression
for idx, sublist in enumerate(data):
    X = np.array(sublist[:8]).reshape(-1, 1)  # Take only the first 8 values corresponding to samples 1 to 8
    y = np.array(mn_values)
    
    # Create and train the model
    model = LinearRegression()
    model.fit(X, y)
    
    # Predict the values
    #y_pred = model.predict(X)
    
    # Calculate R² and RMSE
    r2 = model.score(X,y)
    # Calculate Root Mean Squared Error (RMSE)
    rmse = np.sqrt(mean_squared_error(X,y))
    slope = model.coef_
    intercept = model.intercept_

    for cell in Reference_Spectra_Min_Max: 
        if Sample_Spectra_List[idx] >= cell[0] and Sample_Spectra_List[idx] <= cell[1]:
            results.append({'wavelength': Sample_Spectra_List[idx], 'wavelength_min': Selected_Sample_Spectra_min_list[idx] , 'wavelength_max': Selected_Sample_Spectra_max_list[idx], 'R2': r2, 'RMSE': rmse ,'slope': slope , 'intercept': intercept , 'Index' : idx } )

# # Sort the results by R² in descending order
# sorted_results = sorted(results, key=lambda x: x['R2'], reverse=True)

# Filter the results where slope is positive
filtered_results = [result for result in results if result['slope'] > 0]

# Sort the filtered results by R² in descending order
sorted_filtered_results = sorted(filtered_results, key=lambda x: x['R2'], reverse=True)

# Display the results
df = pd.DataFrame(sorted_filtered_results[:50])
print(df)



   wavelength  wavelength_min  wavelength_max        R2      RMSE  \
0  251.866667      251.666667      251.900000  0.649855  0.688423   
1  251.433333      251.333333      251.466667  0.643661  0.689679   
2  250.600000      250.500000      250.633333  0.570451  0.690717   
3  288.066667      287.933333      288.133333  0.444208  0.694395   
4  413.200000      413.066667      413.266667  0.433097  0.691112   
5  263.066667      262.933333      263.166667  0.330036  0.656963   
6  252.533333      252.433333      252.733333  0.254295  0.667026   

                  slope  intercept  Index  
0     [432.36319220053]  -6.191502     89  
1  [433.58310884864744]  -5.377440     88  
2  [438.80811986548235]  -4.798655     86  
3  [303.34762196831826]  -1.440135    165  
4    [399.277596169186]  -4.134902    301  
5   [212.7650496105748] -13.473947    118  
6   [197.7965310051762]  -9.276875     91  


In [28]:
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score, mean_squared_error
import pandas as pd

# Provided data (as an example, add more sublists as needed)
data_1 = max_peaks_all_ranges


elements_1 = {
    'Element':  [   'C', 'Si',  'Mn',    'P',    'S',  'Cr',  'Mo',  'Ni',  'Al',  'Co',  'Cu',   'Nb',   'Ti',    'V',   'Sn',   'W',   'Zr',   'Pb',    'B'],
    'SAMPLE9':  [0.1222, 0.13, 0.571, 0.0257, 0.0075, 0.550, 0.000, 0.000, 0.280, 0.000, 0.036, 0.0191, 0.0353, 0.0071, 0.0000, 0.000, 0.0065, 0.0000, 0.0016],
    'SAMPLE10': [0.0847, 0.10, 0.489, 0.0156, 0.0140, 0.020, 0.007, 0.000, 0.413, 0.000, 0.101, 0.0000, 0.0086, 0.0038, 0.0000, 0.016, 0.0069, 0.0000, 0.0015],
    'SAMPLE11': [0.2990, 0.32, 0.622, 0.0205, 0.0079, 2.150, 0.126, 0.000, 3.430, 0.000, 0.049, 0.0337, 0.0502, 0.0246, 0.0000, 0.000, 0.0078, 0.0000, 0.0027],
    'SAMPLE12': [0.0032, 0.00, 0.000, 0.0049, 0.0058, 0.000, 0.007, 0.000, 0.000, 0.000, 0.006, 0.0000, 0.0000, 0.0000, 0.000, 0.021, 0.0055, 0.0000, 0.0000],
    'SAMPLE13': [0.2734, 0.09, 0.347, 0.0225, 0.0147, 0.021, 0.008, 0.047, 0.000, 0.000, 0.044, 0.0021, 0.0000, 0.0029, 0.0000, 0.000, 0.0071, 0.0000, 0.0009],
    'SAMPLE14': [0.8027, 0.67, 0.428, 0.0402, 0.0240, 0.591, 0.010, 0.054, 0.775, 0.000, 0.220, 0.0169, 0.0181, 0.0087, 0.0000, 0.000, 0.0091, 0.0000, 0.0019],
    'SAMPLE15': [0.6353, 0.58, 0.473, 0.0415, 0.0238, 0.184, 0.005, 0.075, 1.995, 0.000, 0.430, 0.0136, 0.0158, 0.0061, 0.0120, 0.000, 0.0121, 0.0000, 0.0023],
    'SAMPLE16': [0.6632, 0.33, 0.515, 0.0323, 0.0176, 0.194, 0.021, 0.077, 0.029, 0.000, 1.585, 0.0000, 0.0067, 0.0000, 0.0150, 0.000, 0.0000, 0.0000, 0.0018],
    'SAMPLE17': [0.0943, 0.00, 0.208, 0.0250, 0.0130, 0.007, 0.007, 0.023, 0.000, 0.000, 0.067, 0.0030, 0.0000, 0.0023, 0.0000, 0.000, 0.0071, 0.0000, 0.0005],
}



# Extract 'Mn' values for samples 9 to 18
mn_values_1 = [elements_1[f'SAMPLE{i}'][1] for i in range(9, 18)]
# print(mn_values_1)

results_1 = []

# Loop through each sublist in data and perform linear regression
for idx_1, sublist in enumerate(data_1):
    X_1 = np.array(sublist[8:]).reshape(-1, 1)  # Take only the values corresponding to samples 9 to 17
    y_1 = np.array(mn_values_1)
    
    # Create and train the model
    model_1 = LinearRegression()
    model_1.fit(X_1, y_1)
    
    # Predict the values
    #y_pred = model.predict(X)
    
   # Calculate R² and RMSE
    r2_1 = model_1.score(X_1,y_1)
    # Calculate Root Mean Squared Error (RMSE)
    rmse_1 = np.sqrt(mean_squared_error(X_1,y_1))
    slope_1 = model_1.coef_
    intercept_1 = model_1.intercept_
    for cell_1 in Reference_Spectra_Min_Max: 
        if Sample_Spectra_List[idx_1] >= cell_1[0] and Sample_Spectra_List[idx_1] <= cell_1[1]:
                results_1.append({'wavelength': Sample_Spectra_List[idx_1],'wavelength_min': Selected_Sample_Spectra_min_list[idx_1] , 'wavelength_max': Selected_Sample_Spectra_max_list[idx_1], 'R2': r2_1, 'RMSE': rmse_1 , 'slope': slope_1 , 'intercept': intercept_1, 'Index' : idx_1 } )


# Filter the results where slope is positive
filtered_results_1 = [result for result in results_1 if result['slope'] > 0]

# Sort the filtered results by R² in descending order
sorted_filtered_results_1 = sorted(filtered_results_1, key=lambda x: x['R2'], reverse=True)

# Display the top 50 results
df_1 = pd.DataFrame(sorted_filtered_results_1[:50])
print(df_1)


   wavelength  wavelength_min  wavelength_max        R2      RMSE  \
0  263.066667      262.933333      263.166667  0.374327  0.292023   
1  288.066667      287.933333      288.133333  0.279497  0.334342   
2  519.200000      519.066667      519.300000  0.086544  0.335852   
3  251.866667      251.666667      251.900000  0.017751  0.327932   
4  250.600000      250.500000      250.633333  0.005669  0.330248   
5  251.433333      251.333333      251.466667  0.002296  0.329152   
6  413.200000      413.066667      413.266667  0.001284  0.330659   
7  252.533333      252.433333      252.733333  0.000581  0.304379   

                  slope  intercept  Index  
0   [55.68852592225521]  -3.494424    118  
1   [252.5054247184114]  -1.160804    165  
2   [534.1686101279282]  -1.725678    339  
3   [45.00680467267092]  -0.415396     89  
4   [28.33701984938651]  -0.078973     86  
5  [20.135559315893655]  -0.016180     88  
6   [4.943594209951989]   0.192747    301  
7   [5.285352802397749]  -